In [115]:
import numpy as np
import pandas as pd
import plotly.express as px

# Problem Formulation

We use data from the following competition:
https://www.kaggle.com/competitions/optiver-trading-at-the-close. The dataset contains data on 200 stocks 10 minutes before the close of the trading day at 10 second intervals. This data is recorded over 480 days. Features in the data are all provided by the NASDAQ exchange.

The data was chosen because it is a high-quality, publicly available dataset of stock prices with relatively high frequency. It presents unique challenges due to discontinuities between time intervals (because only the last 10 minutes are recorded), as well as stock identifiers and dates being anonymised.


In [116]:
raw_data = pd.read_parquet("./data_raw/XTrainIntFltCmp.parquet", engine='pyarrow')
target_raw_data = pd.read_parquet("./data_raw/Ytrain.parquet", engine='pyarrow')

The original competition dataset had a "target" label which was a 60 second future move in the weighted average price in the stock, relative to a 60 second future move in weighted index of Nasdaq-listed stocks. Instead, we aim to predict movements of several target stocks - namely their _weighted average price_, which will be described later.

In [117]:
raw_data['target'] = target_raw_data.values
raw_data.head()

stock_id  date_id  seconds_in_bucket  imbalance_size  \
0         0        0                  0      3180602.69   
1         1        0                  0       166603.91   
2         2        0                  0       302879.87   
3         3        0                  0     11917682.27   
4         4        0                  0       447549.96   

   imbalance_buy_sell_flag  reference_price  matched_size  far_price  \
0                        1         0.999812   13380276.64        NaN   
1                       -1         0.999896    1642214.25        NaN   
2                       -1         0.999561    1819368.03        NaN   
3                       -1         1.000171   18389745.62        NaN   
4                       -1         0.999532   17860614.95        NaN   

   near_price  bid_price  bid_size  ask_price   ask_size  wap  time_id  \
0         NaN   0.999812  60651.50   1.000026    8493.03  1.0        0   
1         NaN   0.999896   3233.04   1.000660   20605.09  1.0        0   
2         NaN   0.999403  37956.00   1.000298   18995.00  1.0        0   
3         NaN   0.999999   2324.90   1.000214  479032.40  1.0        0   
4         NaN   0.999394  16485.54   1.000016     434.10  1.0        0   

     target  
0 -3.029704  
1 -5.519986  
2 -8.389950  
3 -4.010200  
4 -7.349849

We need to find a continuous section of time where stock data is available.

In [118]:
# number of windows available
stocks_per_date = raw_data.groupby("date_id").stock_id.nunique().reset_index().rename({"stock_id": "num_stocks"}, axis=1)

px.line(stocks_per_date, x = "date_id", y="num_stocks")

The dataset contains features of an asset related to its price in the Nasdaq closing auction. In the closing auction, buy and sell orders for a stock are collected over 10 minutes. At the 10 minute mark, the market closes and all orders are matched at a single price (using a Nasdaq algorithm). More details can be found at https://www.kaggle.com/code/tomforbes/optiver-trading-at-the-close-introduction.

We are particularly interested in using stock information to predict the weighted average price of assets. Classical time series models require hand-tuned features and at least an a-priori idea of the relationships between covariates; however in this situation all stocks are anonymized. Since we don't have any other options, we try and take advantage of the automatic feature extraction features of deep learning methods.

In [119]:
# stocks present in all time periods. See if we are losing important information by using only these
s = raw_data[["stock_id", "date_id"]].pivot_table(index="stock_id", columns="date_id", aggfunc=len).dropna().index
stocks_always_present = raw_data[raw_data["stock_id"].isin(s)]["stock_id"].unique()

In [120]:
len(stocks_always_present)

188

In [121]:
stocks_no_missing_ticks = raw_data[raw_data["stock_id"].isin(s)]\
.groupby(['stock_id', 'date_id'])['seconds_in_bucket']\
.count().reset_index().groupby("stock_id")["seconds_in_bucket"].sum().reset_index()\
.query("seconds_in_bucket == 26455")["stock_id"]

In [122]:
# stocks with no missing data
df = raw_data.copy()
df_stocks_no_missing = raw_data[raw_data['stock_id'].isin(stocks_no_missing_ticks)]
df_stocks_missing = raw_data[~raw_data['stock_id'].isin(stocks_no_missing_ticks)]

In [123]:
df["no_missing_ticks"] = df["stock_id"].isin(stocks_no_missing_ticks)

In [124]:
average_per_date = df_stocks_no_missing.groupby(["stock_id", "date_id"]).mean().reset_index()

In [125]:
# average WAP over time for all stocks
random_stocks = np.random.choice(stocks_no_missing_ticks, size = 20)

fig = px.line(average_per_date, y = "wap", x = "date_id", color = 'stock_id')
fig.update_traces(opacity = 0.8)
fig.show()

Collections of stocks may have High WAP on certain days; average WAP may display some correlation between stocks. But we don't really care about this - we are primarily concerned with prediction at 10-second intervals.

In [126]:
n_dates = len(df_stocks_no_missing['date_id'].unique())

df_train = df_stocks_no_missing[df_stocks_no_missing['date_id'] < n_dates * 0.9]
df_test = df_stocks_no_missing[df_stocks_no_missing['date_id'] >= n_dates * 0.9]

The prediction problem is unique in that current models (including the baseline that we are implementing) assume continuous data; however, here intervals are of 10 minutes long, followed by a 23-hour 50-minute discontinuity. The model should be able to capture relationships both across and within auction periods.

We have 188 stocks observed over 480 dates and with about 55 observations per date (9 minutes). Each observation has 8 features provided (we can engineer more).

We train on the first 90% of dates (up to date_id 432) and test on the remaining dates.

# EDA

 At this preliminary stage we add the features for every stock - without any understanding of causal relationships between stocks there isn't much justification we can use for adding features of other stocks as indicators, so we just add everything and see whether the model can train.

 (If this is too much, we can switch our focus to predicting a single stock, and then choosing which covariates to add).

## Order book

Each `date_id`, `seconds_in_bucket` pair is uniquely identified by `time_id`. To understand the other features we have to understand how an order book works.

First, a _bid_ of $x$ units of stock at _bid price_ $p$ means that someone is willing to buy $x$ units of stock for at most $p$ units of money each (so they are willing to pay at most $px$ in total). Similarly an _ask_ of $y$ units of stock at _ask price_ $q$ means that someone is willing to sell $y$ of stock for at least $q$ units of money each.

---

Consider the following order book for trading over the trading day:

| Bid | Price | Ask |
|---|---|---|
|   | 5 | 1 |
| 2 | 4 |  |
| 0 | 3 |  |

This means that at a price level of 5, market participants are willing to sell 1 share; at a price level of 4, market participants are willing to buy 2 shares.

At this point, if another participant puts in an ask for 5 shares at the price of 4, then 2 shares would be _matched_, and the order book would update as follows:

| Bid | Price | Ask |
|---|---|---|
|   | 5 | 1 |
|  | 4 | 3 |
| 0 | 3 |  |

Note that the highest bid price will always be lesser than the lowest ask price. Say we have the following situation:

| Bid | Price | Ask |
|---|---|---|
| 1 | 5 | 0 |
| 0 | 4 | 1 |
| 0 | 3 |   |

Then anyone in the market can immediately buy 1 unit of stock at price 4, and then sell it at price 5, making 1 dollar with no risk. This is called an _arbitrage_ opportunity; however, realising this opportunity immediately eliminates the situation from the market:

| Bid | Price | Ask |
|---|---|---|
| 0 | 5 | 0 |
| 0 | 4 | 0 |
| 0 | 3 |   |

---
## Auction Order Book
We mentioned earlier that Nasdaq also collects orders for the _closing auction_ in the last 10 minutes of the trading day. The order book for the closing auction behaves differently from the order book for live trading. To distinguish them, we will call the live trading order book the _live book_ and the auction order book the _auction book_. Orders are collected over the last 10 minutes of the trading day, but are not immediately matched; instead, they are all matched at once during the closing auction. Consider the following auction book:

| Bid | Price | Ask |
|---|---|---|
|   | 5 | 1 |
| 3 | 4 | 2 |
| 4 | 3 | 4 |

In this situation, the highest bid price is not necessarily greater than the lowest ask price, since orders cannot be immediately filled. When an auction book is in this state, it is said to be _in-cross_, and the price determined by the closing auction is called the _uncross_ price, since it is the price at which in-cross orders are matched.

Consider the auction book above, and assume that prices can only take integer values.
- At uncross price 5, 0 lots are matched
- At uncross price 4, 3 lots are matched, since there are 3 bids $\ge 4$ and 6 asks $\le 4$
- At uncross price 3, 4 lots are matched, since there are 7 bids $\ge 3$ and 4 asks $\le 3$.

Since 3 maximizes the number of matched lots, the uncross price is 3, the matched size is 4 and the _imbalance_ (number of unmatched shares) is 3 lots in the buy direction.

### `far_price`
Crucially, the state of the auction book is constantly updated in the last 10 minutes of the trading day as more orders come in. The _far price_ at a particular time is the uncross price of the auction book at that time; it ignores currently ongoing market orders. Nasdaq only provides far price information 5 minutes (300 seconds) before closing time:

In [127]:
# Plot far price of 10 randomly selected stocks for the first date
np.random.seed(0)
random_stocks = np.random.choice(stocks_no_missing_ticks, size = 10)

far_prices = px.line(df_train[df_train["stock_id"].isin(random_stocks)].query("date_id==0"),
              y = "far_price",
              x = "seconds_in_bucket",
              color = 'stock_id')

far_prices.show()

## Combined book

NASDAQ also reports features that are based on the _combined book_, which is just a sum of the live and order book entries across price levels. Summing the live book

| Bid | Price | Ask |
|---|---|---|
|   | 5 | 1 |
| 2 | 4 |  |
| 0 | 3 |  |

and the auction book

| Bid | Price | Ask |
|---|---|---|
|   | 5 | 1 |
| 3 | 4 | 2 |
| 4 | 3 | 4 |

we get the following combined book:

| Bid | Price | Ask |
|---|---|---|
|   | 5 | 2 |
| 5 | 4 | 2 |
| 4 | 3 | 4 |

For the combined book, the uncross price is 4, the matched size is 5, and there is an imbalance of 1 lot in the sell direction.

## `near_price`
_Near price_ is calculated similarly to far price; it is the uncross price of the combined book at a particular time. Like far price, NASDAQ only provides near price information 5 minutes before closing time. Plotting the near price of the same stocks, we can see that they track fair prices quite closely.

In [128]:
from plotly.subplots import make_subplots
import plotly.graph_objects as go

near_prices = px.line(df_train[df_train["stock_id"].isin(random_stocks)].query("date_id==0"),
              y = "near_price",
              x = "seconds_in_bucket",
              color = 'stock_id')

near_prices.show()

## `bid_price / ask_price`
These features denote the "most competitive" price in the live book. For bids, this is the highest bid price; for asks, this is the lowest bid price. Recall that in the live book, `bid_price` should always be less than `ask_price`.

In [129]:
fig = px.line(df_train[df_train["stock_id"].isin(random_stocks)].query("date_id==0"),
              y = ["bid_price", "ask_price"],
              x = "seconds_in_bucket",
              color = 'stock_id')

for gr in fig['data']:
    if gr['showlegend']:
        gr['line']['dash'] = 'dash'

fig.show()

In the diagram above, the dashed line is `bid_price` and the solid line is `ask_price`. We see that bid price is consistently lower than ask price for all stocks. However, the gap between bid and ask varies across both stocks and times. This is called the _bid-ask spread_, and is used as a measure of liquidity in the market for the asset.

## `bid_size / ask_size`
The number of stocks being offered at that corresponding price. These correspond to the table entries in the live book.

## `wap`
Weighted average price in the live book - our main prediction target for each stock. It follows the following formula:

$$ \frac{\text{bid\_price} * \text{ask\_size} + \text{ask\_price} * \text{bid\_size}}{\text{bid\_size} + \text{ask\_size}} $$

WAP is renormalized so that it is 1.0 for the first time step of each (stock_id, date_id) combination; all other prices are renormalized relative to this.

In [130]:
df_train.query("seconds_in_bucket == 0").query("wap != 1")

Empty DataFrame
Columns: [stock_id, date_id, seconds_in_bucket, imbalance_size, imbalance_buy_sell_flag, reference_price, matched_size, far_price, near_price, bid_price, bid_size, ask_price, ask_size, wap, time_id, target]
Index: []

## `reference_price`
NASDAQ provides an indicator for the fair price called the _reference price_.


$$
\text{reference\_price} = \begin{cases}\text{best\_ask} &\text{ if near\_price } > \text{best\_ask} \\
\text{best\_bid} &\text{ if near\_price } < \text{best bid}
\\ \text{near\_price} &\text{ if }\text{best\_bid } \le \text{ near\_price } \le \text{best\_ask }
\end{cases}
$$

Notice that reference price is provided for all times, not just in the last 5 minutes. The calculation for near_price in the first 5 minutes uses only the live book instead of the combined book. NASDAQ uses reference price at each time to determine the proceeding features:

## `matched_size`
Amount that can be matched at the current reference price.
## `imbalance_size`
Amount that is unmatched at the current reference price.
## `imbalance_buy_sell_flag`
1 if there is an excess of buy orders; -1 if there is an excess of sell orders; 0 if there is no imbalance.

# Prepare training and test data

In [131]:
def rename_features(df):
    df = df.rename({"date_id": "window_id", "seconds_in_bucket": "time"}, axis=1)
    return df

def impute_near_far(df): # replace near and far data NA values with 0.
    return df.fillna(0)

def reshape_df(df):
    df = df.drop(["time_id"], axis = 1)
    df = df.set_index(['stock_id', 'window_id', 'time']).unstack(['stock_id'])
    df = df.reindex(columns=sorted(df.columns, key=lambda x: x[::-1]))
    df.columns = ["{}_{}".format(t,v) for t,v in df.columns]
    df = df.reset_index()
    return df

def add_indicators(df):
    df["last_5_mins"] = np.where(df["time"] >= 300, 1, 0) # Indicator for whether near and far data are valid.
    return df

def TAKE_OUT_TIME_STEP(df):
    # This should be replaced with a compute_covariate function.
    df = df.drop(["time"], axis = 1)
    return df


In [132]:
df_train = df_train.pipe(rename_features)\
    .pipe(impute_near_far)\
    .pipe(reshape_df)\
    .pipe(add_indicators)\
    .pipe(TAKE_OUT_TIME_STEP)

df_test = df_test.pipe(rename_features)\
    .pipe(impute_near_far)\
    .pipe(reshape_df)\
    .pipe(add_indicators)\
    .pipe(TAKE_OUT_TIME_STEP)

#### The original TimeGrad paper adds extra covariates for time index - but we ignore them for now.

In [133]:
import torch
from torch.utils.data import Dataset, DataLoader

In [134]:
class StockDataset(Dataset):
    """
    To preserve original window structure, do not shuffle, and set batch size to be 55.
    """
    def __init__ (self, df):
        self.target_cols = [col for col in df if col.startswith("target")] # we have to change this when we add lags
        self.feature_cols = [col for col in df if not col.startswith("target") and not col.startswith("window_id")]
        self.labels = df[self.target_cols] # labels for all stocks at all times
        self.features = df[self.feature_cols]
    def __len__(self):
        return len(self.labels)
    def __getitem__(self, idx):
        return self.features.iloc[idx].values, self.labels.iloc[idx].values

In [135]:
df_train.to_pickle('./data_postprocessing/train_df.pkl')
df_test.to_pickle('./data_postprocessing/test_df.pkl')

In [136]:
train_dataset = StockDataset(df_train)
torch.save(train_dataset, './data_postprocessing/train.pt')
test_dataset = StockDataset(df_test)
torch.save(test_dataset, './data_postprocessing/test.pt')